In [1]:
import numpy as np
import csv
import os
import math
import random

In [2]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [3]:
class cellpoint:
  frame: int
  id: int
  posx: int
  posy: int

In [4]:
def GetFreq(AnnotData):
  for cell_id in AnnotData.keys():
    if len(AnnotData[cell_id])>1:
      return AnnotData[cell_id][1].frame-AnnotData[cell_id][0].frame 
  return 1

In [5]:
def CalculateMovements(AnnotData, Robustness, Frequency):
  SumMovements = 0
  SumDistances = 0
  NumElements = 0
  CellMovements = []

  for cell_id in AnnotData.keys():
    if len(AnnotData[cell_id])>1:
      prevx = AnnotData[cell_id][0].posx
      prevy = AnnotData[cell_id][0].posy
      StartFrame = AnnotData[cell_id][1].frame
      MaxDist = 0
      CurrentMovement = 0
      counter = 0
      for element in AnnotData[cell_id]:
        if np.mod(counter,Frequency)-np.mod(StartFrame,Frequency)==0:
          CurrentMovement += np.sqrt(np.power(element.posx-prevx,2)+np.power(element.posy-prevy,2))
          NumElements += 1
          prevx = element.posx
          prevy = element.posy
          DistFromZeroPos = np.sqrt(np.power(element.posx-AnnotData[cell_id][0].posx,2)+np.power(element.posy-AnnotData[cell_id][0].posy,2))
          if DistFromZeroPos>MaxDist:
            MaxDist = DistFromZeroPos
        counter+=1
      SumDistances += MaxDist
      CellMovements.append(CurrentMovement)

  if NumElements==0:
    return [-1,-1]

  #Applying robust mean
  CellMovements.sort()
  if Robustness != 0:
    NumData = len(CellMovements)
    CellMovements = CellMovements[math.ceil(NumData*Robustness/100):math.floor(NumData-NumData*Robustness/100)]
  SumMovements = sum(CellMovements)

  SumMovements /= NumElements
  SumDistances /= NumElements
  return [SumMovements, SumDistances]

In [6]:
def UnitVector(vector):
    return vector / np.linalg.norm(vector)

def AngleBetween(v1, v2):
    v1_u = UnitVector(v1)
    v2_u = UnitVector(v2)
    return np.arccos(np.clip(np.dot(v1_u, v2_u), -1.0, 1.0))

def CalculateAngles(AnnotData, Robustness, Frequency):
  CellAngles = []
  NumElements = 0
  for cell_id in AnnotData.keys():
    if len(AnnotData[cell_id])>2:
      pprevx = AnnotData[cell_id][0].posx
      pprevy = AnnotData[cell_id][0].posy
      prevx = AnnotData[cell_id][1].posx
      prevy = AnnotData[cell_id][1].posy
      StartFrame = AnnotData[cell_id][2].frame
      CurrentAngles = 0
      counter = 0
      for element in AnnotData[cell_id]:
        if counter>1 and np.mod(counter,Frequency)-np.mod(StartFrame,Frequency)==0:
          Angle = AngleBetween([prevx-pprevx, prevy-pprevy],[element.posx-prevx, element.posy-prevy])
          if not math.isnan(Angle):
            CurrentAngles += Angle
          pprevx = prevx
          pprevy = prevy
          prevx = element.posx
          prevy = element.posy
          NumElements += 1
        counter+=1
      CellAngles.append(CurrentAngles)

  if NumElements==0:
    return -1

  #Applying robust mean
  CellAngles.sort()
  if Robustness != 0:
    NumData = len(CellAngles)
    CellAngles = CellAngles[math.ceil(NumData*Robustness/100):math.floor(NumData-NumData*Robustness/100)]
  SumAngles = sum(CellAngles)/NumElements

  return SumAngles

def CalculateNormAngles(AnnotData, Robustness, Frequency):
  CellAngles = []
  NumElements = 0
  for cell_id in AnnotData.keys():
    if len(AnnotData[cell_id])>2:
      pprevx = AnnotData[cell_id][0].posx
      pprevy = AnnotData[cell_id][0].posy
      prevx = AnnotData[cell_id][1].posx
      prevy = AnnotData[cell_id][1].posy
      StartFrame = AnnotData[cell_id][2].frame
      CurrentAngles = 0
      counter = 0
      for element in AnnotData[cell_id]:
        if counter>1 and np.mod(counter,Frequency)-np.mod(StartFrame,Frequency)==0:
          #Angle = AngleBetween([prevx-pprevx, prevy-pprevy],[element.posx-prevx, element.posy-prevy])*(np.sqrt(np.power(pprevx-prevx,2)+np.power(pprevy-prevy,2))+np.sqrt(np.power(prevx-element.posx,2)+np.power(prevy-element.posy,2)))
          Angle = AngleBetween([prevx-pprevx, prevy-pprevy],[element.posx-prevx, element.posy-prevy])*np.sqrt(np.power(pprevx-element.posx,2)+np.power(pprevy-element.posy,2))
          if not math.isnan(Angle):
            CurrentAngles += Angle
          pprevx = prevx
          pprevy = prevy
          prevx = element.posx
          prevy = element.posy
          NumElements += 1
        counter+=1
      CellAngles.append(CurrentAngles)
  
  if NumElements==0:
    return -1

  #Applying robust mean
  CellAngles.sort()
  if Robustness != 0:
    NumData = len(CellAngles)
    CellAngles = CellAngles[math.ceil(NumData*Robustness/100):math.floor(NumData-NumData*Robustness/100)]
  SumAngles = sum(CellAngles)/NumElements

  return SumAngles

In [7]:
def ReadData(CellType,NameModifier, HumanDataFolder, ComputerDataFolder):
  HumanAnnotPath = HumanDataFolder+CellType+".path"
  ComputerAnnotPath = ComputerDataFolder+CellType+NameModifier+".txt"

  HumanAnnotFile = open(HumanAnnotPath,"r") 
  ComputerAnnotFile = open(ComputerAnnotPath,"r") 

  HumanAnnotList = HumanAnnotFile.readlines()
  ComputerAnnotList = ComputerAnnotFile.readlines()

  HumanAnnotData = {}
  ComputerAnnotData = {}

  for row in HumanAnnotList:
    splitted = row.split(' ')
    cellp = cellpoint()
    if splitted[0].isdigit():
      cellp.posx = int(splitted[0])
      cellp.posy = int(splitted[1])
      cellp.frame = int(splitted[2])
      cellp.id = int(splitted[3].strip())
      if not (cellp.id in HumanAnnotData):
        HumanAnnotData[cellp.id]=[]
        HumanAnnotData[cellp.id].append(cellp)
      else:
        HumanAnnotData[cellp.id].append(cellp)

  for row in ComputerAnnotList:
    splitted = row.split('\t')
    cellp = cellpoint()
    if splitted[0].isdigit():
      cellp.frame = int(splitted[0].strip())
      cellp.id = int(splitted[1].strip())
      cellp.posx = int(splitted[2].strip())
      cellp.posy = int(splitted[3].strip())
      if not (cellp.id in ComputerAnnotData):
        ComputerAnnotData[cellp.id]=[]
        ComputerAnnotData[cellp.id].append(cellp)
      else:
        ComputerAnnotData[cellp.id].append(cellp)

  return[HumanAnnotData, ComputerAnnotData]
      

In [8]:
def RandomSampleForAnnotData(AnnotData,Num):
  random.seed()
  Numbers = range(len(AnnotData))
  Samples = random.sample(Numbers,Num)
  i = 0
  ReducedAnnotData={}
  for cell_id in AnnotData.keys():
    if i in Samples:
      ReducedAnnotData[cell_id]=AnnotData[cell_id]
    i+=1
  return ReducedAnnotData

In [9]:
#Listing all the videos in a folder

AvailableVideos = os.listdir('/content/drive/My Drive/Colab Notebooks/CellTracking/MSC Diplomamunka/Validisation2/Validisation data/01 Videos')
CellTypes = []
for CurrentVideo in AvailableVideos:
  splitted = CurrentVideo.split('.')
  CellTypes.append(splitted[0])
CellTypes.sort()
for CellType in CellTypes:
  print(CellType)

BIBF06_10
BIBF_01_16
BIBF_01_7
BIBF_03_16
BIBF_03_6
aktivin01_2
aktivin01_3
hipox03_2
melanoma_GF01_11
zometa01_4
zometa01_6
zometa02_4
zometa03_3
zometa03_5
zometa06_3


In [10]:
#MAIN CODE

#CellTypes = ['BIBF_01_7','aktivin01_2','aktivin01_3','hipox03_2','melanoma_GF01_11','zometa01_4']
HumanDataFolder = "/content/drive/My Drive/Colab Notebooks/CellTracking/MSC Diplomamunka/Validisation2/Validisation data/02 Human Annotations/"
ComputerDataFolder = "/content/drive/My Drive/Colab Notebooks/CellTracking/MSC Diplomamunka/Validisation2/Validisation data/03 Estimated Paths/"
OutCSVPath = "/content/drive/My Drive/Colab Notebooks/CellTracking/MSC Diplomamunka/Validisation2/Results/Precision.csv"
NameModifier = "_in_human_annot_range"
SamplingExp=1.2
NumOfTrials=100

with open(OutCSVPath, mode='w') as CSVfile:
  CSVwriter = csv.writer(CSVfile, delimiter=',', quotechar='"', quoting=csv.QUOTE_MINIMAL)
  CSVwriter.writerow(["CellType","SampleAmount","MeanDiffOfMovements","MeanDiffOfDistances","MeanDiffOfAngles",
                      "DeviationOfMovements","DeviationOfDistances","DeviationOfAngles"])
  
  for CellType in CellTypes:
    #Reading both files
    [HumanAnnotData, ComputerAnnotData] = ReadData(CellType,NameModifier,HumanDataFolder,ComputerDataFolder)

    HumanAnnotFreq = GetFreq(HumanAnnotData)

    print(CellType +"\t\tMax num of samples: "+np.str(len(ComputerAnnotData)))

    [ComputerSumMovementsFreq, ComputerSumDistancesFreq] = CalculateMovements(ComputerAnnotData,0,HumanAnnotFreq)
    ComputerSumAnglesFreq = CalculateNormAngles(ComputerAnnotData,0,HumanAnnotFreq)

    Num = 1
    while Num < len(ComputerAnnotData):
      AllCompMov = []
      AllCompDist = []
      AllCompAng = []
      for Trial in range(NumOfTrials):
        ReducedComputerAnnotData = RandomSampleForAnnotData(ComputerAnnotData, Num)
        if len(ReducedComputerAnnotData)>0:
          #Calculating the movements for both data

          [RComputerSumMovementsFreq, RComputerSumDistancesFreq] = CalculateMovements(ReducedComputerAnnotData,0,HumanAnnotFreq)
          RComputerSumAnglesFreq = CalculateNormAngles(ReducedComputerAnnotData,0,HumanAnnotFreq)

          if RComputerSumAnglesFreq != -1 or RComputerSumMovementsFreq != -1:
            AllCompMov.append(np.absolute(ComputerSumMovementsFreq-RComputerSumMovementsFreq))
            AllCompDist.append(np.absolute(ComputerSumDistancesFreq-RComputerSumDistancesFreq))
            AllCompAng.append(np.absolute(ComputerSumAnglesFreq-RComputerSumAnglesFreq))

      CSVwriter.writerow([CellType,Num,np.mean(AllCompMov),np.mean(AllCompDist),np.mean(AllCompAng),
                          np.std(AllCompMov),np.std(AllCompDist),np.std(AllCompAng)])
      Num *=SamplingExp
      Num = int(np.ceil(Num))

    

BIBF06_10		Max num of samples: 61


/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:2: RuntimeWarning: invalid value encountered in true_divide
  


BIBF_01_16		Max num of samples: 601
BIBF_01_7		Max num of samples: 1495
BIBF_03_16		Max num of samples: 1032
BIBF_03_6		Max num of samples: 123
aktivin01_2		Max num of samples: 377
aktivin01_3		Max num of samples: 404
hipox03_2		Max num of samples: 115
melanoma_GF01_11		Max num of samples: 179
zometa01_4		Max num of samples: 40
zometa01_6		Max num of samples: 194
zometa02_4		Max num of samples: 198
zometa03_3		Max num of samples: 627
zometa03_5		Max num of samples: 300
zometa06_3		Max num of samples: 111
